In [3]:
import astropy.io.fits as fits
import numpy as np
import matplotlib.pyplot as plt
from scipy.optimize import curve_fit
from scipy import asarray as ar,exp
from scipy import ndimage
import random
from scipy import ndimage
from scipy.optimize import least_squares
from func import *
from scipy import stats
from matplotlib.colors import LogNorm
from scipy.optimize import leastsq
from matplotlib import cm
plt.rcParams['font.family'] = 'Serif'
plt.rcParams['font.weight'] = 'light'

In [4]:
def nan_free_data(filename):
    hdu = fits.open(filename)
    qso_data = hdu[0].data
    qso_error = hdu[1].data
    qso_header = hdu[0].header
    wavestart = qso_header['CRVAL3']
    wavint = qso_header['CD3_3']
    wave = wavestart+np.arange(qso_data.shape[0])*wavint#. This is the same as the one below.
    qso_data[np.isnan(qso_data)] = 0.0000001
    qso_error[np.isnan(qso_error)] = 0.000001
    return qso_data,qso_error,wave,qso_header

In [5]:
def fit(x,y,y_err):
    (popt2,pcov2) = leastsq(full_gauss_eline,x0=[0.1,0.2,12588,50,0.01,0.02,12488,100,0.0001,0.002],args = (x,y,y_err),maxfev=10000000)
    print (popt2)
    return popt2

def MC(x,y,y_err,MC_loops=0):
    popt_MC = np.stack(fit(x,np.random.normal(y,y_err),y_err) for l in range(MC_loops))
    err = np.nanstd(popt_MC,0)
    return err

In [6]:
def eline_tab(obj,par,par_err,cor,destination_path_cube='/Volumes/Seagate'):
    amp_Hb = np.stack(x[0] for x in par)
    amp_OIII = np.stack(x[1] for x in par)
    vel_OIII = np.stack(x[2] for x in par)
    vel_sigma_OIII = np.stack(x[3] for x in par)
    amp_Hb_br = np.stack(x[4] for x in par)
    amp_OIII_br = np.stack(x[5] for x in par)
    vel_OIII_br = np.stack(x[6] for x in par)
    vel_sigma_OIII_br = np.stack(x[7] for x in par)

    amp_Hb_err = np.stack(x[0] for x in par_err)
    amp_OIII_err = np.stack(x[1] for x in par_err)
    vel_OIII_err = np.stack(x[2] for x in par_err)
    vel_sigma_OIII_err = np.stack(x[3] for x in par_err)
    amp_Hb_br_err = np.stack(x[4] for x in par_err)
    amp_OIII_br_err = np.stack(x[5] for x in par_err)
    vel_OIII_br_err = np.stack(x[6] for x in par_err)
    vel_sigma_OIII_br_err = np.stack(x[7] for x in par_err)
    
    x_cor = np.stack(x[0] for x in cor)
    y_cor = np.stack(y[1] for y in cor)
    
    c1 = fits.Column(name='x_cor', array=x_cor, format='K')
    c2 = fits.Column(name='y_cor', array=y_cor, format='K')
    c3 = fits.Column(name='amp_Hb', array=amp_Hb, format='E')
    c4 = fits.Column(name='amp_OIII', array=amp_OIII, format='E')
    c5 = fits.Column(name='vel_OIII', array=vel_OIII, format='E')
    c6 = fits.Column(name='vel_sigma_OIII', array=vel_sigma_OIII, format='E')
    c7 = fits.Column(name='amp_Hb_br', array=amp_Hb_br, format='E')
    c8 = fits.Column(name='vel_OIII', array=amp_OIII_br, format='E')
    c9 = fits.Column(name='vel_OIII', array=vel_OIII_br, format='E')
    c10 = fits.Column(name='vel_OIII', array=vel_sigma_OIII_br, format='E')

    t = fits.BinTableHDU.from_columns([c1, c2, c3, c4, c5, c6, c7, c8, c9, c10])

    t.writeto('%s/%s Extended/table_%s_extended_double_gauss.fits'%(destination_path_cube,obj,obj),overwrite=True)

In [7]:
def err_maps(obj,par_err,destination_path_cube='/Volumes/Seagate'):
    hdus=[]
    hdus.append(fits.PrimaryHDU())
    hdus.append(fits.ImageHDU(par_err[0,:,:],name='amp_Hb'))
    hdus.append(fits.ImageHDU(par_err[1,:,:],name='amp_OIII'))
    hdus.append(fits.ImageHDU(par_err[2,:,:],name='vel_OIII'))
    hdus.append(fits.ImageHDU(par_err[3,:,:],name='vel_sigma_OIII'))
    hdus.append(fits.ImageHDU(par_err[4,:,:],name='amp_Hb_br'))
    hdus.append(fits.ImageHDU(par_err[5,:,:],name='amp_OIII_br'))
    hdus.append(fits.ImageHDU(par_err[6,:,:],name='vel_OIII_br'))
    hdus.append(fits.ImageHDU(par_err[7,:,:],name='vel_sigma_OIII_br'))
    hdus.append(fits.ImageHDU(par_err[8,:,:],name='m'))
    hdus.append(fits.ImageHDU(par_err[9,:,:],name='c'))
    hdu = fits.HDUList(hdus)

    hdu.writeto('%s/%s Extended/subcube_par_err_%s_extended_double_gauss.fits'%(destination_path_cube,obj,obj),overwrite=True)

In [8]:
def algorithm_script(obj,z,destination_path_cube = '/Volumes/Seagate'):
    (qso_data,qso_error,wave,qso_header) =  nan_free_data('%s/%s Extended/%s.extended_cube.fits'%(destination_path_cube,obj,obj))   
    popt = np.stack(fit(wave,qso_data[:,i,j],qso_error[:,i,j]) for i in range(qso_data.shape[1]) for j in range(qso_data.shape[2]))
    err = np.stack(MC(wave,qso_data[:,i,j],qso_error[:,i,j],10) for i in range(qso_data.shape[1]) for j in range(qso_data.shape[2]))
    cor = np.stack((i,j) for i in range(qso_data.shape[1]) for j in range(qso_data.shape[2]))           

    eline_tab(obj,par,par_err,cor)
    #filecubename = '%s/%s Extended/subcube_par_%s_extended_fitted_residual_2Gauss.fits'%(destination_path_cube.obj,obj)
    #store_cube(filecubename,fitted,wave,residuals,qso_header)

In [9]:
z = {"HE0040-1105":0.04196}

objs = z.keys()

for obj in objs:
    algorithm_script(obj,z[obj])


/opt/anaconda3/lib/python3.7/site-packages/IPython/core/interactiveshell.py:3331: FutureWarning: arrays to stack must be passed as a "sequence" type such as list or tuple. Support for non-sequence iterables such as generators is deprecated as of NumPy 1.16 and will raise an error in the future.
  exec(code_obj, self.user_global_ns, self.user_ns)


[-2.27430887e-04  1.17620501e-03  1.25449407e+04 -4.75972857e-03
  1.00000000e-02  2.00000000e-02  1.24880000e+04  1.00000000e+02
  1.05660808e-03 -5.55629525e-03]
[ 1.17237864e-03 -1.68657451e-03  1.30622475e+04  1.99589379e+02
  1.00000000e-02  2.00000000e-02  1.24880000e+04  1.00000000e+02
  1.44458713e-03 -7.59144602e-03]
[-1.74378324e-03  1.18913819e-03  1.25174851e+04 -8.55903440e-04
  1.00000000e-02  2.00000000e-02  1.24880000e+04  1.00000000e+02
 -7.19043511e-04  3.63144750e-03]
[-9.79112959e-04  1.57573413e-03  1.25318136e+04  5.90078152e+01
  1.00000000e-02  2.00000000e-02  1.24880000e+04  1.00000000e+02
  2.91062852e-03 -1.53591570e-02]
[-8.95175505e-04  1.10919609e-03  1.18647998e+04 -3.88502686e+02
  1.00000000e-02  2.00000000e-02  1.24880000e+04  1.00000000e+02
  1.52348592e-03 -8.18544053e-03]
[ 2.88673946e-03 -9.35737461e-04  1.27252131e+04 -6.12199445e+01
  1.00000000e-02  2.00000000e-02  1.24880000e+04  1.00000000e+02
  2.09765295e-03 -1.09957061e-02]
[ 1.63763016e-03

[ 1.99346095e-03  8.26104107e-04  1.25899946e+04  1.49487733e-02
  1.00000000e-02  2.00000000e-02  1.24880000e+04  1.00000000e+02
  9.02889960e-04 -4.91691643e-03]
[ 1.21103606e-03 -2.18954073e-03  1.24510633e+04 -2.31518489e-03
  1.00000000e-02  2.00000000e-02  1.24880000e+04  1.00000000e+02
 -7.07340651e-04  3.39308269e-03]
[ 9.37172196e-04  1.41951007e-03  1.21768040e+04 -2.26538236e+02
  1.00000000e-02  2.00000000e-02  1.24880000e+04  1.00000000e+02
  2.82074986e-04 -1.84535746e-03]
[ 3.63697813e-04  1.89260706e-03  1.28116576e+04  3.25702417e+02
  1.00000000e-02  2.00000000e-02  1.24880000e+04  1.00000000e+02
 -2.55562431e-04  9.54443550e-04]
[-1.56625945e-03  7.21082173e-04  1.25181959e+04  5.47506361e+01
  1.00000000e-02  2.00000000e-02  1.24880000e+04  1.00000000e+02
  2.39523339e-03 -1.24425035e-02]
[ 1.20132779e-03  3.01664495e-03  1.25703673e+04  5.43235641e-02
  1.00000000e-02  2.00000000e-02  1.24880000e+04  1.00000000e+02
 -1.99761171e-04  8.20043068e-04]
[ 2.15754640e-03

  8.63660663e-04 -4.44132013e-03]
[ 1.42476026e-03 -3.75242496e-04  1.27209974e+04 -1.42788754e-02
  1.00000000e-02  2.00000000e-02  1.24880000e+04  1.00000000e+02
 -4.77454336e-04  2.19480953e-03]
[-1.93794417e-03 -3.21132343e-04  1.25383888e+04  1.71108729e-02
  1.00000000e-02  2.00000000e-02  1.24880000e+04  1.00000000e+02
 -6.39959300e-04  3.17449447e-03]
[ 1.45130331e-03 -1.80966593e-03  1.26972478e+04  2.47151784e-02
  1.00000000e-02  2.00000000e-02  1.24880000e+04  1.00000000e+02
  7.54476808e-04 -4.09354649e-03]
[ 1.57095567e-03  1.65401513e-03  1.25087517e+04 -1.55796402e-02
  1.00000000e-02  2.00000000e-02  1.24880000e+04  1.00000000e+02
 -7.24878118e-04  3.20993802e-03]
[ 5.51042267e-06  2.22852412e-03  1.26344456e+04  1.00026014e+02
  1.00000000e-02  2.00000000e-02  1.24880000e+04  1.00000000e+02
  7.49641342e-04 -3.94948310e-03]
[-2.02575073e-03  2.22593263e-03  1.22899465e+04  6.56376464e-02
  1.00000000e-02  2.00000000e-02  1.24880000e+04  1.00000000e+02
  7.01793201e-04

[ 1.50263753e-03 -1.95319964e-04  1.25704470e+04  4.02485513e+01
  1.00000000e-02  2.00000000e-02  1.24880000e+04  1.00000000e+02
  5.73017439e-04 -3.29253072e-03]
[-7.21552795e-04 -1.59371579e-03  1.26820178e+04 -3.83449404e-03
  1.00000000e-02  2.00000000e-02  1.24880000e+04  1.00000000e+02
 -4.29601693e-04  1.97881472e-03]
[ 1.96004428e-04  1.70047910e-03  1.30377060e+04 -1.47715417e+02
  1.00000000e-02  2.00000000e-02  1.24880000e+04  1.00000000e+02
 -1.10003111e-03  5.55338624e-03]
[ 1.90641863e-03  1.97454219e-03  1.21031487e+04  5.59478689e-04
  1.00000000e-02  2.00000000e-02  1.24880000e+04  1.00000000e+02
 -2.21579800e-03  1.10459318e-02]
[ 1.32552424e-03 -1.85242623e-03  1.27505820e+04  1.95157292e-03
  1.00000000e-02  2.00000000e-02  1.24880000e+04  1.00000000e+02
 -1.01297206e-03  4.89088173e-03]
[-1.91880164e-03  8.42218159e-04  1.24732988e+04 -2.41768278e-02
  1.00000000e-02  2.00000000e-02  1.24880000e+04  1.00000000e+02
 -1.58524176e-03  7.64579896e-03]
[ 9.43772733e-04

...

[ 1.08852350e-03  2.82632097e-03  1.26267224e+04  1.61342552e+02
  1.00000000e-02  2.00000000e-02  1.24880000e+04  1.00000000e+02
  1.38237690e-03 -7.20664056e-03]
[-3.95697018e-04  3.09100168e-03  1.25076492e+04  1.23021849e+02
  1.00000000e-02  2.00000000e-02  1.24880000e+04  1.00000000e+02
 -1.89276681e-04  7.89769085e-04]
[-2.12577509e-03  3.62419262e-03  1.24245165e+04  9.11129075e+01
  1.00000000e-02  2.00000000e-02  1.24880000e+04  1.00000000e+02
 -2.36047725e-05  4.27156359e-05]
[-9.09860777e-04  2.87288408e-03  1.25094490e+04  1.70588520e+02
  1.00000000e-02  2.00000000e-02  1.24880000e+04  1.00000000e+02
  5.61425469e-04 -2.99115200e-03]
[ 2.07161096e-03  3.86604941e-03  1.25248127e+04  4.12234641e+01
  1.00000000e-02  2.00000000e-02  1.24880000e+04  1.00000000e+02
  1.05998596e-03 -5.65518579e-03]
[-2.16749596e-05  3.13563855e-03  1.25309832e+04  1.57435386e+02
  1.00000000e-02  2.00000000e-02  1.24880000e+04  1.00000000e+02
  9.92078415e-04 -5.30969837e-03]
[ 4.26821180e-04

  1.18814129e-03 -6.05823854e-03]
[ 1.09661617e-03  7.73668122e-03  1.25618212e+04  1.47772383e+02
  1.00000000e-02  2.00000000e-02  1.24880000e+04  1.00000000e+02
 -2.60695336e-04  1.37407449e-03]
[ 1.96299488e-03  7.70687087e-03  1.25633837e+04  1.10138570e+02
  1.00000000e-02  2.00000000e-02  1.24880000e+04  1.00000000e+02
  2.36030663e-03 -1.21016517e-02]
[ 2.45661346e-03  7.31945492e-03  1.25807970e+04  1.31656325e+02
  1.00000000e-02  2.00000000e-02  1.24880000e+04  1.00000000e+02
  7.98980004e-04 -4.11383018e-03]
[ 1.72238451e-03  8.69156104e-03  1.25707979e+04  1.21115482e+02
  1.00000000e-02  2.00000000e-02  1.24880000e+04  1.00000000e+02
  9.98693838e-04 -5.13750932e-03]
[ 1.48251034e-03  8.45030493e-03  1.25560777e+04  1.13159389e+02
  1.00000000e-02  2.00000000e-02  1.24880000e+04  1.00000000e+02
  6.87983330e-04 -3.41750100e-03]
[ 7.81236489e-04  6.75016189e-03  1.25829838e+04  1.34439727e+02
  1.00000000e-02  2.00000000e-02  1.24880000e+04  1.00000000e+02
 -2.60689341e-04

 -5.02204474e-04  2.04532077e-03]
[-7.65547713e-04  7.11701263e-03  1.25975518e+04  4.55994774e+01
  1.00000000e-02  2.00000000e-02  1.24880000e+04  1.00000000e+02
  2.64346780e-04 -1.63781033e-03]
[ 6.94973774e-04  7.38540351e-03  1.25841065e+04  3.85769474e+01
  1.00000000e-02  2.00000000e-02  1.24880000e+04  1.00000000e+02
  9.12796788e-04 -4.97531953e-03]
[ 2.49357713e-03  4.43643954e-03  1.25862832e+04  1.10757216e+02
  1.00000000e-02  2.00000000e-02  1.24880000e+04  1.00000000e+02
 -7.59898192e-05  1.10877009e-04]
[ 2.16902654e-03  8.69425031e-03  1.25969569e+04  7.72717613e+01
  1.00000000e-02  2.00000000e-02  1.24880000e+04  1.00000000e+02
 -5.42845493e-04  2.38219782e-03]
[ 2.46358150e-03  7.40742565e-03  1.25685007e+04  7.51750748e+01
  1.00000000e-02  2.00000000e-02  1.24880000e+04  1.00000000e+02
  3.48295142e-04 -2.16389518e-03]
[ 1.88742644e-03  6.17908161e-03  1.25733886e+04  3.26744656e+01
  1.00000000e-02  2.00000000e-02  1.24880000e+04  1.00000000e+02
  5.02143293e-04

[ 4.12806828e-04  4.13254257e-03  1.26034405e+04  1.23071635e+02
  1.00000000e-02  2.00000000e-02  1.24880000e+04  1.00000000e+02
  2.28579042e-03 -1.18033489e-02]
[ 1.31133191e-03  4.02504426e-03  1.26100766e+04  1.29476674e+02
  1.00000000e-02  2.00000000e-02  1.24880000e+04  1.00000000e+02
  2.39622113e-03 -1.24702246e-02]
[-1.69315606e-03  3.46771159e-03  1.25694452e+04  9.60817418e+01
  1.00000000e-02  2.00000000e-02  1.24880000e+04  1.00000000e+02
  1.91843374e-03 -9.77541963e-03]
[ 1.02662771e-03  2.82567410e-03  1.26420363e+04  2.28542790e+02
  1.00000000e-02  2.00000000e-02  1.24880000e+04  1.00000000e+02
  2.07666654e-03 -1.06780120e-02]
[ 1.66117959e-03  2.20148796e-03  1.26331021e+04  1.20741439e-02
  1.00000000e-02  2.00000000e-02  1.24880000e+04  1.00000000e+02
  1.12810154e-04 -6.04569150e-04]
[ 2.09693198e-03  3.01550189e-03  1.24978289e+04  2.97350797e+01
  1.00000000e-02  2.00000000e-02  1.24880000e+04  1.00000000e+02
 -4.19000317e-04  2.12396993e-03]
[-3.41868614e-04

KeyboardInterrupt: 

In [ ]:
amp_Hb = np.stack(x[0] for x in r)
amp_OIII = np.stack(x[1] for x in r)
vel_OIII = np.stack(x[2] for x in r)
vel_sigma_OIII = np.stack(x[3] for x in r)
m = np.stack(x[8] for x in r)
c = np.stack(x[9] for x in r)
OIII_Hb_ratio = amp_OIII/amp_Hb

In [ ]:
np.shape(OIII_Hb_ratio)

In [ ]:
amp_Hb_err = np.stack(x[0] for x in err)
amp_OIII_err = np.stack(x[1] for x in err)
vel_OIII_err = np.stack(x[2] for x in err)
vel_sigma_OIII_err = np.stack(x[3] for x in err)
m_err = np.stack(x[8] for x in err)
c_err = np.stack(x[9] for x in err)

In [ ]:
np.shape(amp_OIII_err)

In [ ]:
x_cor = np.stack(x[0] for x in cor)
y_cor = np.stack(y[1] for y in cor)

In [ ]:
gas_select = (amp_OIII / amp_OIII_err > 7)

In [ ]:
OIII_flux_map = np.full((dim[1],dim[2]) ,np.nan)
OIII_flux_map[x_cor[gas_select],y_cor[gas_select]] = amp_OIII[gas_select]

In [ ]:

fig = plt.figure()

ax = plt.axes([0,0,1,1])

#cmap=cm.inferno
cmap = sns.cubehelix_palette(100, light=0.95,dark=0.15, as_cmap=True)
cmap.set_bad('w',1) # Make the NANs white

frame = plt.imshow(OIII_flux_map, origin='lower', cmap=cmap, norm=LogNorm(), interpolation='None')
cbar = plt.colorbar()
cbar.set_label(r"[OIII] Surface Brightness ($\times 10^{-16}$ erg s$^{-1}$ cm$^{-2}$ $\AA^{-1}$)")

In [ ]:
OIII_vel_map = np.full((dim[1],dim[2]) ,np.nan)
OIII_vel_map[x_cor[gas_select],y_cor[gas_select]] = vel_OIII[gas_select] - vel_syst[gas_select]

In [ ]:
fig = plt.figure()

ax = plt.axes([0,0,1,1])


cmap = cm.RdBu_r
cmap.set_bad('black',1) # Make the NANs white

frame = plt.imshow(OIII_vel_map, origin='lower', cmap=cmap, vmin=-50,vmax=50, interpolation='None')
cbar = plt.colorbar()
cbar.set_label(r"[OIII] Velocity (km/s)")

In [ ]:
OIII_vel_sigma_map = np.full((dim[1],dim[2]) ,np.nan)
OIII_vel_sigma_map[x_cor[gas_select],y_cor[gas_select]] = vel_sigma_OIII[gas_select] #- vel_syst[gas_select]

In [ ]:
fig = plt.figure()

ax = plt.axes([0,0,1,1])


cmap = cm.Reds

cmap.set_bad('k',1) # Make the NANs white

frame = plt.imshow(OIII_vel_sigma_map, origin='lower', cmap=cmap, vmin=0,vmax=200, interpolation='None')
cbar = plt.colorbar()
cbar.set_label(r"[OIII] Velocity Dispersion (km/s)")

In [ ]:
ionization_map = np.full((dim[1],dim[2]) ,np.nan)
ionization_map[x_cor[gas_select],y_cor[gas_select]] = OIII_Hb_ratio[gas_select] 

In [ ]:
fig = plt.figure()

ax = plt.axes([0,0,1,1])


cmap = sns.cubehelix_palette(100, light=0.95,dark=0.15, as_cmap=True)
cmap = cm.Reds
cmap.set_bad('w',1) # Make the NANs white

frame = plt.imshow(ionization_map, origin='lower', cmap=cmap, vmin=0.1,vmax=15, interpolation='nearest')
cbar = plt.colorbar()
cbar.set_label(r"[OIII]/H$\beta$")